In [ ]:
# import necessary dependencies
import argparse
import os, sys
import time
import datetime
from tqdm import tqdm_notebook as tqdm

import os
import torch
import torch.nn as nn
import pandas as pd
from skimage import io, transform
import numpy as np
import matplotlib.pyplot as plt
from torch.utils.data import Dataset, DataLoader
from torchvision import transforms, utils
import torchvision

# Ignore warnings
import warnings
warnings.filterwarnings("ignore")

In [ ]:
BATCH_SIZE = 128
EPOCHS = 100
#DECAY = 5e-4
#MOMENTUM = 0.9
LR = 5e-3

In [ ]:
class RotNet(nn.Module):
    def __init__(self):
        super(RotNet, self).__init__()
        self.encoder = torchvision.models.resnet18(pretrained=False)
        self.encoder.conv1 = nn.Conv2d(3, 64, kernel_size=3, stride=1, padding=1, bias=False)
        self.encoder.maxpool = nn.Identity()
        self.encoder.fc = nn.Identity()
        self.linear1 = nn.Linear(512, 4, bias=False)

    def forward(self, x):
        out = self.encoder(x)
        out = self.linear1(out)

        return out

In [ ]:
class CIFAR10Rot(Dataset):

    def __init__(self, base_dataset):

        self.base_dataset = base_dataset
        self.transformed = self.rot()

    def rot(self):
        roted_x = []
        roted_y = []
        for img, _ in tqdm(self.base_dataset):
            for idx, angle in enumerate([0, 90, 180, 270]):
                rot_im = torchvision.transforms.functional.rotate(img, angle)
                rot_label = idx

                roted_x.append(rot_im)
                roted_y.append(rot_label)

        return roted_x, roted_y


    def __len__(self):
        return len(self.base_dataset) * 4

    def __getitem__(self, idx):
        return self.transformed[0][idx], self.transformed[1][idx]

In [ ]:
train_transform = transforms.Compose(
    [transforms.Resize(size=(32, 32)),
    transforms.ToTensor()]
)
test_transform = transforms.Compose(
    [transforms.Resize(size=(32, 32)),
    transforms.ToTensor()]
)
trainset = torchvision.datasets.CIFAR10(root='./data', train=True, download=True, transform=train_transform)
trainset = CIFAR10Rot(trainset)

trainloader = torch.utils.data.DataLoader(trainset, batch_size=BATCH_SIZE, shuffle=True, num_workers=0)

testset = CIFAR10Rot(torchvision.datasets.CIFAR10(root='./data', train=False, download=True, transform=test_transform))
testloader = torch.utils.data.DataLoader(testset, batch_size=BATCH_SIZE, shuffle=False, num_workers=0)

classes = ('plane', 'car', 'bird', 'cat', 'deer', 'dog', 'frog', 'horse', 'ship', 'truck')

100%|██████████| 170498071/170498071 [00:01<00:00, 102311761.15it/s]


Extracting ./data/cifar-10-python.tar.gz to ./data


  0%|          | 0/50000 [00:00<?, ?it/s]

Files already downloaded and verified


  0%|          | 0/10000 [00:00<?, ?it/s]

In [ ]:
criterion = nn.CrossEntropyLoss()

In [ ]:
rot_model = RotNet().cuda()
#optimizer = torch.optim.SGD(rot_model.parameters(), lr=LR, momentum=MOMENTUM, weight_decay=DECAY)
optimizer = torch.optim.Adam(rot_model.parameters(), lr=LR)
scheduler = torch.optim.lr_scheduler.MultiStepLR(optimizer, milestones=[30, 60, 80], gamma=0.2)



best_loss = 9999999

for epoch_idx in range(EPOCHS):
    epoch_losses = 0
    epoch_corrects = 0
    rot_model.train()
    for batch_idx, data in enumerate(tqdm(trainloader)):
        image, label = data
        image = image.cuda()
        label = label.cuda()

        rot_model.zero_grad()
        out = rot_model(image)

        loss = criterion(out, label)
        loss.backward()
        optimizer.step()

        epoch_losses += loss

        pred = torch.argmax(out, dim=1)
        epoch_corrects += torch.sum(pred == label).item()

    epoch_losses /= len(trainloader)
    epoch_corrects /= len(trainset)


    with torch.no_grad():
        rot_model.eval()

        test_epoch_losses = 0
        test_epoch_corrects = 0

        for batch_idx, data in enumerate(tqdm(testloader)):
            image, label = data
            image = image.cuda()
            label = label.cuda()

            out = rot_model(image)

            loss = criterion(out, label)

            test_epoch_losses += loss

            pred = torch.argmax(out, dim=1)
            test_epoch_corrects += torch.sum(pred == label).item()

        test_epoch_losses /= len(testloader)
        test_epoch_corrects /= len(testset)

        if test_epoch_losses < best_loss:
            best_loss = test_epoch_losses
            torch.save(rot_model.state_dict(), f'rotnet_base_{EPOCHS}_{BATCH_SIZE}_{LR}.pth')

    scheduler.step()
    print(f'Train Loss {epoch_losses} Acc {epoch_corrects} ; Val Loss {test_epoch_losses} Acc {test_epoch_corrects}')

  0%|          | 0/1563 [00:00<?, ?it/s]

  0%|          | 0/313 [00:00<?, ?it/s]

Train Loss 0.9846785068511963 Acc 0.58179 ; Val Loss 0.839855432510376 Acc 0.649975


  0%|          | 0/1563 [00:00<?, ?it/s]

  0%|          | 0/313 [00:00<?, ?it/s]

...

  0%|          | 0/313 [00:00<?, ?it/s]

Train Loss 5.805557066196343e-07 Acc 1.0 ; Val Loss 1.2569704055786133 Acc 0.89005


  0%|          | 0/1563 [00:00<?, ?it/s]

  0%|          | 0/313 [00:00<?, ?it/s]

Train Loss 5.731528176511347e-07 Acc 1.0 ; Val Loss 1.2755249738693237 Acc 0.890125


In [ ]:
class RotNet_linear_eval(nn.Module):
    def __init__(self, encoder):
        super(RotNet_linear_eval, self).__init__()
        self.encoder = encoder
        self.linear = nn.Linear(512, 10, bias=False)
        self.relu = nn.ReLU()

        for param in self.encoder.parameters():
            param.requires_grad = False

    def forward(self, x):
        out = self.encoder(x)
        out = self.linear(out)
        return out

In [ ]:
BATCH_SIZE = 192
EPOCHS = 50
DECAY = 5e-4
MOMENTUM = 0.9
LR = 0.01

In [ ]:

train_transform = transforms.Compose(
    [transforms.Resize(size=(32, 32)),
    transforms.ToTensor()]
)
test_transform = transforms.Compose(
    [transforms.Resize(size=(32, 32)),
    transforms.ToTensor()]
)
trainset = torchvision.datasets.CIFAR10(root='./data', train=True, download=True, transform=train_transform)
trainloader = torch.utils.data.DataLoader(trainset, batch_size=BATCH_SIZE, shuffle=True, num_workers=0)

testset = torchvision.datasets.CIFAR10(root='./data', train=False, download=True, transform=test_transform)
testloader = torch.utils.data.DataLoader(testset, batch_size=BATCH_SIZE, shuffle=False, num_workers=0)

classes = ('plane', 'car', 'bird', 'cat', 'deer', 'dog', 'frog', 'horse', 'ship', 'truck')

In [ ]:
criterion = nn.CrossEntropyLoss()

In [ ]:
rot_model = RotNet()
rot_model.load_state_dict(torch.load(pretrained_path))
rot_model.cuda()

rot_linear_eval_model = RotNet_linear_eval(rot_model.encoder)
#rot_linear_eval_model.load_state_dict(torch.load("models/rot_model_semi_sup_30_128_0.001_0.1.pth"))
rot_linear_eval_model.cuda()

#optimizer = torch.optim.SGD(rot_linear_eval_model.parameters(), lr=LR, momentum=MOMENTUM, weight_decay=DECAY)
optimizer = torch.optim.Adam(rot_linear_eval_model.parameters(), lr=LR)
#scheduler = torch.optim.lr_scheduler.MultiStepLR(optimizer, milestones=[20, 40, 60, 80], gamma=0.2)
scheduler = torch.optim.lr_scheduler.StepLR(optimizer, step_size=10, gamma=0.2)

best_loss = 9999999

for epoch_idx in range(EPOCHS):
    epoch_losses = 0
    epoch_corrects = 0
    rot_linear_eval_model.train()
    for batch_idx, data in enumerate(tqdm(trainloader)):
        image, label = data
        image = image.cuda()
        label = label.cuda()

        rot_linear_eval_model.zero_grad()
        out = rot_linear_eval_model(image)

        loss = criterion(out, label)
        loss.backward()
        optimizer.step()

        epoch_losses += loss

        pred = torch.argmax(out, dim=1)
        epoch_corrects += torch.sum(pred == label).item()

    epoch_losses /= len(trainloader)
    epoch_corrects /= len(trainset)


    with torch.no_grad():
        rot_linear_eval_model.eval()

        test_epoch_losses = 0
        test_epoch_corrects = 0

        for batch_idx, data in enumerate(tqdm(testloader)):
            image, label = data
            image = image.cuda()
            label = label.cuda()

            out = rot_linear_eval_model(image)

            loss = criterion(out, label)

            test_epoch_losses += loss

            pred = torch.argmax(out, dim=1)
            test_epoch_corrects += torch.sum(pred == label).item()

        test_epoch_losses /= len(testloader)
        test_epoch_corrects /= len(testset)

        if test_epoch_losses < best_loss:
            best_loss = test_epoch_losses
            torch.save(rot_linear_eval_model.state_dict(), f'rot_model_resnet18_linear_eval_{EPOCHS}_{BATCH_SIZE}_{LR}.pth')

    scheduler.step()
    print(f'Epochs {epoch_idx} Train Loss {epoch_losses} Acc {epoch_corrects} ; Val Loss {test_epoch_losses} Acc {test_epoch_corrects}')

In [ ]:

BATCH_SIZE = 128
EPOCHS = 30
#DECAY = 5e-4
#MOMENTUM = 0.9
LR = 1e-2
label_percentage = 0.01

In [ ]:
class RotNet_linear_eval(nn.Module):
    def __init__(self, encoder):
        super(RotNet_linear_eval, self).__init__()
        self.encoder = encoder
        self.linear = nn.Linear(512, 10, bias=False)

    def forward(self, x):
        out = self.encoder(x)
        out = self.linear(out)
        return out


In [ ]:
train_transform = transforms.Compose(
    [transforms.Resize(size=(32, 32)),
    transforms.ToTensor()]
)
test_transform = transforms.Compose(
    [transforms.Resize(size=(32, 32)),
    transforms.ToTensor()]
)
trainset = torchvision.datasets.CIFAR10(root='./data', train=True, download=True, transform=train_transform)
trainset, _ = torch.utils.data.random_split(trainset, [int(len(trainset)*label_percentage), int(len(trainset)*(1-label_percentage))])

trainloader = torch.utils.data.DataLoader(trainset, batch_size=BATCH_SIZE, shuffle=True, num_workers=0)

testset = torchvision.datasets.CIFAR10(root='./data', train=False, download=True, transform=test_transform)
testloader = torch.utils.data.DataLoader(testset, batch_size=BATCH_SIZE, shuffle=False, num_workers=0)

classes = ('plane', 'car', 'bird', 'cat', 'deer', 'dog', 'frog', 'horse', 'ship', 'truck')

Files already downloaded and verified
Files already downloaded and verified


In [ ]:
criterion = nn.CrossEntropyLoss()

In [ ]:

from torch.optim import optimizer
rot_model = RotNet()
rot_model.load_state_dict(torch.load("rotnet_base_100_128_0.005.pth"))
rot_model.cuda()

rot_linear_eval_model = RotNet_linear_eval(rot_model.encoder)
rot_linear_eval_model.cuda()

#optimizer = torch.optim.SGD(rot_linear_eval_model.parameters(), lr=LR, momentum=MOMENTUM, weight_decay=DECAY)
optimizer = torch.optim.Adam(rot_linear_eval_model.parameters(), lr=LR)
scheduler = torch.optim.lr_scheduler.MultiStepLR(optimizer, milestones=[10, 20], gamma=0.1)

best_loss = 9999999

for epoch_idx in range(EPOCHS):
    epoch_losses = 0
    epoch_corrects = 0
    rot_linear_eval_model.train()
    for batch_idx, data in enumerate(tqdm(trainloader)):
        image, label = data
        image = image.cuda()
        label = label.cuda()

        rot_linear_eval_model.zero_grad()
        out = rot_linear_eval_model(image)

        loss = criterion(out, label)
        loss.backward()
        optimizer.step()

        epoch_losses += loss

        pred = torch.argmax(out, dim=1)
        epoch_corrects += torch.sum(pred == label).item()

    epoch_losses /= len(trainloader)
    epoch_corrects /= len(trainset)


    with torch.no_grad():
        rot_linear_eval_model.eval()

        test_epoch_losses = 0
        test_epoch_corrects = 0

        for batch_idx, data in enumerate(tqdm(testloader)):
            image, label = data
            image = image.cuda()
            label = label.cuda()

            out = rot_linear_eval_model(image)

            loss = criterion(out, label)

            test_epoch_losses += loss

            pred = torch.argmax(out, dim=1)
            test_epoch_corrects += torch.sum(pred == label).item()

        test_epoch_losses /= len(testloader)
        test_epoch_corrects /= len(testset)

        if test_epoch_losses < best_loss:
            best_loss = test_epoch_losses
            torch.save(rot_linear_eval_model.state_dict(), f'rot_model_res18_semi_sup_{EPOCHS}_{BATCH_SIZE}_{LR}_{label_percentage}.pth')

    scheduler.step()
    print(f'Epoch {epoch_idx} Train Loss {epoch_losses} Acc {epoch_corrects} ; Val Loss {test_epoch_losses} Acc {test_epoch_corrects}')

  0%|          | 0/4 [00:00<?, ?it/s]

  0%|          | 0/79 [00:00<?, ?it/s]

Epoch 0 Train Loss 2.1365230083465576 Acc 0.284 ; Val Loss 1.9067717790603638 Acc 0.2948


  0%|          | 0/4 [00:00<?, ?it/s]

  0%|          | 0/79 [00:00<?, ?it/s]

...

  0%|          | 0/79 [00:00<?, ?it/s]

Epoch 28 Train Loss 0.00038126902654767036 Acc 1.0 ; Val Loss 2.0772244930267334 Acc 0.5865


  0%|          | 0/4 [00:00<?, ?it/s]

  0%|          | 0/79 [00:00<?, ?it/s]

Epoch 29 Train Loss 0.0007211256888695061 Acc 1.0 ; Val Loss 2.0805137157440186 Acc 0.5858


In [ ]:
BATCH_SIZE = 128
EPOCHS = 30
#DECAY = 5e-4
#MOMENTUM = 0.9
LR = 1e-2
label_percentage = 0.1

In [ ]:
from torch.optim import optimizer
rot_model = RotNet()
rot_model.load_state_dict(torch.load("rotnet_base_100_128_0.005.pth"))
rot_model.cuda()

rot_linear_eval_model = RotNet_linear_eval(rot_model.encoder)
rot_linear_eval_model.cuda()

#optimizer = torch.optim.SGD(rot_linear_eval_model.parameters(), lr=LR, momentum=MOMENTUM, weight_decay=DECAY)
optimizer = torch.optim.Adam(rot_linear_eval_model.parameters(), lr=LR)
scheduler = torch.optim.lr_scheduler.MultiStepLR(optimizer, milestones=[10, 20], gamma=0.1)

best_loss = 9999999

for epoch_idx in range(EPOCHS):
    epoch_losses = 0
    epoch_corrects = 0
    rot_linear_eval_model.train()
    for batch_idx, data in enumerate(tqdm(trainloader)):
        image, label = data
        image = image.cuda()
        label = label.cuda()

        rot_linear_eval_model.zero_grad()
        out = rot_linear_eval_model(image)

        loss = criterion(out, label)
        loss.backward()
        optimizer.step()

        epoch_losses += loss

        pred = torch.argmax(out, dim=1)
        epoch_corrects += torch.sum(pred == label).item()

    epoch_losses /= len(trainloader)
    epoch_corrects /= len(trainset)


    with torch.no_grad():
        rot_linear_eval_model.eval()

        test_epoch_losses = 0
        test_epoch_corrects = 0

        for batch_idx, data in enumerate(tqdm(testloader)):
            image, label = data
            image = image.cuda()
            label = label.cuda()

            out = rot_linear_eval_model(image)

            loss = criterion(out, label)

            test_epoch_losses += loss

            pred = torch.argmax(out, dim=1)
            test_epoch_corrects += torch.sum(pred == label).item()

        test_epoch_losses /= len(testloader)
        test_epoch_corrects /= len(testset)

        if test_epoch_losses < best_loss:
            best_loss = test_epoch_losses
            torch.save(rot_linear_eval_model.state_dict(), f'rot_model_res18_semi_sup_{EPOCHS}_{BATCH_SIZE}_{LR}_{label_percentage}.pth')

    scheduler.step()
    print(f'Epoch {epoch_idx} Train Loss {epoch_losses} Acc {epoch_corrects} ; Val Loss {test_epoch_losses} Acc {test_epoch_corrects}')

  0%|          | 0/40 [00:00<?, ?it/s]

  0%|          | 0/79 [00:00<?, ?it/s]

Epoch 0 Train Loss 1.2371128797531128 Acc 0.5592 ; Val Loss 1.348272442817688 Acc 0.5908


  0%|          | 0/40 [00:00<?, ?it/s]

  0%|          | 0/79 [00:00<?, ?it/s]

...

  0%|          | 0/79 [00:00<?, ?it/s]

Epoch 28 Train Loss 0.006026883609592915 Acc 0.9998 ; Val Loss 1.2003147602081299 Acc 0.7424


  0%|          | 0/40 [00:00<?, ?it/s]

  0%|          | 0/79 [00:00<?, ?it/s]

Epoch 29 Train Loss 0.0018757205689325929 Acc 1.0 ; Val Loss 1.1988903284072876 Acc 0.7448


In [ ]:
color_jitter = torchvision.transforms.ColorJitter(
        0.4, 0.4, 0.4, 0.1
    )
train_transform = torchvision.transforms.Compose(
    [
        transforms.RandomResizedCrop(size=(32, 32)),
        transforms.RandomHorizontalFlip(p=0.5),
        transforms.RandomApply([color_jitter], p=0.8),
        torchvision.transforms.RandomGrayscale(p=0.2),
        transforms.ToTensor(),
    ]
)

test_transform = transforms.Compose(
    [transforms.Resize(size=(32, 32)),
    transforms.ToTensor()]
)

In [ ]:
trainset = torchvision.datasets.CIFAR10(root='/usr/xtmp/zg78/cifar10_data/', train=True, download=True, transform=train_transform)
trainloader = torch.utils.data.DataLoader(trainset, batch_size=BATCH_SIZE, shuffle=True, num_workers=0)

testset = torchvision.datasets.CIFAR10(root='/usr/xtmp/zg78/cifar10_data/', train=False, download=True, transform=test_transform)
testloader = torch.utils.data.DataLoader(testset, batch_size=BATCH_SIZE, shuffle=False, num_workers=0)

100%|██████████| 170498071/170498071 [00:13<00:00, 12966949.71it/s]


Extracting /usr/xtmp/zg78/cifar10_data/cifar-10-python.tar.gz to /usr/xtmp/zg78/cifar10_data/
Files already downloaded and verified


In [ ]:
criterion = nn.CrossEntropyLoss()

In [ ]:
net = torchvision.models.resnet18().cuda()
optimizer = torch.optim.SGD(net.parameters(), lr=0.01, momentum=0.9)

best_loss = 9999999

for epoch_idx in range(EPOCHS):
    epoch_losses = 0
    epoch_correts = 0
    net.train()
    for batch_idx, data in enumerate(tqdm(trainloader)):
        image, label = data
        image = image.cuda()
        label = label.cuda()

        net.zero_grad()
        out = net(image)

        loss = criterion(out, label)
        loss.backward()
        optimizer.step()

        epoch_losses += loss

        pred = torch.argmax(out, dim=1)
        epoch_correts += torch.sum(pred == label).item()

    epoch_losses /= len(trainloader)
    epoch_correts /= len(trainset)


    with torch.no_grad():
        net.eval()

        val_epoch_losses = 0
        val_epoch_correts = 0

        for batch_idx, data in enumerate(tqdm(testloader)):
            image, label = data
            image = image.cuda()
            label = label.cuda()

            out = net(image)

            loss = criterion(out, label)

            val_epoch_losses += loss

            pred = torch.argmax(out, dim=1)
            val_epoch_correts += torch.sum(pred == label).item()

        val_epoch_losses /= len(testloader)
        val_epoch_correts /= len(testset)

        if val_epoch_losses < best_loss:
            best_loss = val_epoch_losses
            torch.save(net.state_dict(), f'resent18_baseline_{EPOCHS}_{BATCH_SIZE}_{LR}.pth')

    print(f'Train Loss {epoch_losses} Acc {epoch_correts} ; Val Loss {val_epoch_losses} Acc {val_epoch_correts}')

  0%|          | 0/391 [00:00<?, ?it/s]

  0%|          | 0/79 [00:00<?, ?it/s]

Train Loss 2.0843257904052734 Acc 0.26268 ; Val Loss 1.6110310554504395 Acc 0.4182


  0%|          | 0/391 [00:00<?, ?it/s]

  0%|          | 0/79 [00:00<?, ?it/s]

...

  0%|          | 0/391 [00:00<?, ?it/s]

  0%|          | 0/79 [00:00<?, ?it/s]

Train Loss 1.3152536153793335 Acc 0.54068 ; Val Loss 1.0293368101119995 Acc 0.6557


  0%|          | 0/391 [00:00<?, ?it/s]

KeyboardInterrupt: ignored